In [123]:
import geemap
import ee
# Trigger the authentication flow.
ee.Authenticate()
# Initialize the library.
ee.Initialize()

Enter verification code:  4/1AbUR2VPtN_ae4906uJyna9n64uQ2n0aKlHtNnR-kXbehjRvCr51DvAsvLw0



Successfully saved authorization token.


In [194]:
#Pandas modules to interact with spatial data
import geopandas as gpd
import pandas as pd
from geopandas import GeoDataFrame
from shapely.geometry import Point,Polygon
from geemap import geopandas_to_ee

from pygeosys.util.dataframe import chunk_dataframe
from generate_data_ee import *
import numpy as np
from functools import reduce

# Initial Parameters

In [186]:
### Parameters
year=2021
date_start = str(year)+'-01-01' # fall tillage : 08-01 to 11-01 ; spring tillage : 02-01 to 05-01
date_end = str(year)+'-12-01'
date_start

'2021-01-01'

In [187]:
# Interactive map - for selecting particular position AOI
Map = geemap.Map(center=[48.853760  ,2.372189],zoom=14 , height=600)
# S1_GRD - raw image - S1_GRD_FLOAT  (raw + preprocessing)
collection = ee.ImageCollection('COPERNICUS/S1_GRD')                        
image = collection.median()
vis = {
    'min': 0.0,
    'max': 3000,
    'bands': ['HH', 'HV', 'angle'],
}
Map.setCenter(1.445045, 43.603516, 15)
Map.addLayer(image, vis, 'Sentinel-1')
#Map


Map(center=[43.603516, 1.445045], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(…

In [249]:
Map.user_roi.getInfo()

AttributeError: 'NoneType' object has no attribute 'getInfo'

In [250]:
from shapely.geometry import Polygon

# AOI polygon 
# Replace the information this below
polygon = ee.Geometry.Polygon(
    #[[[1.443458, 43.605878], [1.441913, 43.602366], [1.447449, 43.598388], [1.455345, 43.602957], [1.452212, 43.607525], [1.443458, 43.605878]]],None,False
     #[[[1.432664, 43.581407],[1.430217, 43.580117],[1.431183, 43.57721],[1.433415, 43.575577],[1.434853, 43.577552],[1.434939, 43.580567],[1.433007, 43.581329],[1.432664, 43.581407]]],None,False
     [[[-54.22460833, -25.36857278],[-54.22041628 ,-25.36727596],[-54.22000322, -25.36748923],[-54.21999249,-25.36769282],[-54.22011831, -25.36807353],[-54.21995738, -25.36860671],[-54.22328332,-25.36968277],[-54.22438839, -25.36971185],[-54.22460833,-25.36857278]]],None,False
)
#(-54.22460833 -25.36857278,-54.22041628 -25.36727596,-54.22000322 -25.36748923,-54.21999249 -25.36769282,-54.22011831 -25.36807353,-54.21995738 -25.36860671,-54.22328332 -25.36968277,-54.22438839 -25.36971185,-54.22460833 -25.36857278)
polyFeature = ee.Feature(polygon, {'foo': 42, 'bar': 'tart'})
Map.addLayer(polyFeature, {} , 'feature')
Map

Map(bottom=12886082.0, center=[38.481359983466746, -100.49147235324536], controls=(WidgetControl(options=['pos…

# Self-Generation

In [154]:
def maskS2clouds(image): 
    qa = image.select('QA60')  

In [155]:
'''
#.filterDate('2020-01-01', '2020-01-30')
#// Pre-filter to get less cloudy granules.
20->75
'''
### Import the Collection with the selected area + the start and end date
im_col = ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')\
                .filterBounds(polygon)\
                .filterDate(ee.Date(date_start),ee.Date(date_end))\
                .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE',75))\
                #.map(maskS2clouds)
im_col# ee.imagecollection.ImageCollection

In [156]:
### Define cloud and shadow mask and apply it
#im_col = im_col.map(add_cld_shdw_mask).map(apply_cld_shdw_mask)

In [157]:
## get available dates 
import time
acq_times = im_col.aggregate_array('system:time_start').getInfo()
len([time.strftime('%x', time.gmtime(acq_time/1000)) for acq_time in acq_times])

38

## Multi-image dowloading

In [147]:
# For multiple downloading image
imList=im_col.select('B4','B8A').toList(im_col.size())
for im in range(imList.length().getInfo()):
    img = ee.Image(imList.get(im))
    task=ee.batch.Export.image.toCloudStorage(**{ 'image': img.clip(polygon), 
                                                 'description': 'Toulouse Multispectral', 
                                                 'bucket': 'datascience-sandbox-dev', #bucket name never changes 
                                                 'fileNamePrefix':'LE/ChangeDetection/MultiSpectral/Image' + str(im),#path to file 
                                                 'scale': 10,#resolution 
                                                 'region':polygon, 
                                                 'maxPixels': 15000000000, 
                                                 'skipEmptyTiles': True }) 
    task.start()

In [143]:
img

## Single Image

In [158]:
# Get first image of collection 
img = ee.Image(im_col.select('B4','B8A').first()) 
img #ee.image.Image

In [161]:
# Get first image of collection for dowloading - displaying
task=ee.batch.Export.image.toCloudStorage(**{
          'image': img.clip(polygon),
          'description': 'Toulouse MultiSpectral Test',
          'bucket': 'datascience-sandbox-dev', #bucket name never changes
          'fileNamePrefix':'LE/ChangeDetection/MultiSpectral/Image_Test' ,#path to file
          'scale': 10,#resolution
          'region':polygon,
          'maxPixels': 15000000000,
          'skipEmptyTiles': True
          })
task.start()

# Generate by using "Generate_data_ee.py"
- See moree at https://developers.google.com/earth-engine/tutorials/community/sentinel-2-s2cloudless

In [251]:
def get_s2_sr_cld_col(aoi, start_date, end_date):
    # Import and filter S2 SR.
    CLOUD_FILTER = 40
    s2_sr_col = (ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
        .filterBounds(aoi)
        .filterDate(start_date, end_date)
        .filter(ee.Filter.lte('CLOUDY_PIXEL_PERCENTAGE', CLOUD_FILTER)))\
        .select('B3', 'B4','B8','QA60','SCL')

    # Import and filter s2cloudless.
    s2_cloudless_col = (ee.ImageCollection('COPERNICUS/S2_CLOUD_PROBABILITY')
        .filterBounds(aoi)
        .filterDate(start_date, end_date))

    # Join the filtered s2cloudless collection to the SR collection by the 'system:index' property.
    return ee.ImageCollection(ee.Join.saveFirst('s2cloudless').apply(**{
        'primary': s2_sr_col,
        'secondary': s2_cloudless_col,
        'condition': ee.Filter.equals(**{
            'leftField': 'system:index',
            'rightField': 'system:index'
        })
    }))


In [252]:
# polygon - date_start - date_end
s2_sr_cld_col = get_s2_sr_cld_col(polygon, date_start, date_end)  # ('B3', 'B4','B8','QA60','SCL')
s2_sr_cld_col

In [253]:
### Define cloud and shadow mask and apply it
s2_sr_cld_col = s2_sr_cld_col.map(add_cld_shdw_mask).map(apply_cld_shdw_mask) 
s2_sr_cld_col

In [254]:
# Select the particular band for dowloading 
red_nir_col = s2_sr_cld_col.select('B4','B8')
red_nir_col

In [255]:
## get available dates 
import time
acq_times = red_nir_col.aggregate_array('system:time_start').getInfo()
len([time.strftime('%x', time.gmtime(acq_time/1000)) for acq_time in acq_times])

74

## Single-file Dowloading

In [256]:
# Red -B4 and NIR-B8A - 
im_list = red_nir_col.toList(red_nir_col.size())
# Take the 1st image
img = ee.Image(red_nir_col.select('B4','B8').first()) 
img

In [257]:
# Get first image of collection for dowloading - displaying
task=ee.batch.Export.image.toCloudStorage(**{
          'image': img.clip(polygon),
          'description': 'Toulouse MultiSpectral Images',
          'bucket': 'datascience-sandbox-dev', #bucket name never changes
          'fileNamePrefix':'LE/ChangeDetection/MultiSpectral/ImageT' ,#path to file
          'scale': 10,#resolution
          'region':polygon,
          'maxPixels': 15000000000,
          'skipEmptyTiles': True
          })
task.start()

## Multiple downloading 

In [ ]:
# For multiple downloading image
# Get a list of image for dowloading
imList=red_nir_col.select('B4','B8').toList(red_nir_col.size())
for im in range(imList.length().getInfo()):
    img = ee.Image(imList.get(im))
    task=ee.batch.Export.image.toCloudStorage(**{ 'image': img.clip(polygon), 
                                                 'description': 'Toulouse Multispectral', 
                                                 'bucket': 'datascience-sandbox-dev', #bucket name never changes 
                                                 'fileNamePrefix':'LE/ChangeDetection/MultiSpectral/' + str(im),#path to file 
                                                 'scale': 10,#resolution 
                                                 'region':polygon, 
                                                 'maxPixels': 15000000000, 
                                                 'skipEmptyTiles': True }) 
    task.start()